In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings 
from datetime import datetime

In [2]:
pd.set_option('display.max_rows', None)  
pd.set_option('display.max_columns', None) 

warnings.filterwarnings('ignore')

df = pd.read_csv("train.csv")
df.head()

Basvuru Yili  Degerlendirme Puani Cinsiyet  Dogum Tarihi        Dogum Yeri  \
0          2014                 52.0    Erkek      4/6/1994  Altindag, Ankara   
1          2014                 30.0    Erkek     6/11/1993           Üsküdar   
2          2014                 18.0    Erkek     1/15/1986            Samsun   
3          2014                 40.0    Erkek      6/4/1991        Diyarbakır   
4          2014                 24.0    Erkek  2 Kasim 1992   Ankara/Altındağ   

  Ikametgah Sehri                    Universite Adi Universite Turu  \
0          Ankara           İHSAN DOĞRAMACI BİLKENT            Özel   
1        İstanbul           İHSAN DOĞRAMACI BİLKENT            Özel   
2        İstanbul  ULUSLARARASI KIBRIS ÜNİVERSİTESİ            Özel   
3        İstanbul       İSTANBUL ŞEHİR ÜNİVERSİTESİ            Özel   
4          Ankara          TURGUT ÖZAL ÜNİVERSİTESİ            Özel   

   Burslu ise Burs Yuzdesi Burs Aliyor mu?  \
0                    100.0            Evet   
1                    100.0           Hayır   
2                    100.0           Hayır   
3                    100.0            Evet   
4                    100.0            Evet   

                                      Bölüm Universite Kacinci Sinif  \
0                   Bilgisayar Muhendisligi                        3   
1          Elektrik Elektronik Mühendisliği                        3   
2              Finans Yönetimi ve Pazarlama                        1   
3                   Bilgisayar Mühendisliği                        3   
4  Siyaset Bilimi ve Uluslararası ilişkiler                      NaN   

  Universite Not Ortalamasi Daha Once Baska Bir Universiteden Mezun Olmus  \
0                    3.50-3                                         Hayır   
1                 3.00-2.50                                         Hayır   
2                       NaN                                         Hayır   
3                 3.00-2.50                                         Hayır   
4                 3.00-2.50                                         Hayır   

                        Lise Adi Lise Adi Diger  Lise Sehir       Lise Turu  \
0  Ankara Ataturk Anadolu Lisesi            NaN      Ankara  Anadolu lisesi   
1       Betül Can Anadolu Lisesi            NaN      Ankara  Anadolu lisesi   
2                          Batem            NaN      Ankara   Meslek lisesi   
3          Cumhuriyet Fen Lisesi            NaN  Diyarbakır      Fen lisesi   
4               Samanyolu Lisesi            NaN      Ankara     Özel lisesi   

  Lise Bolumu Lise Bolum Diger Lise Mezuniyet Notu  \
0          MF              NaN              3.50-3   
1          MF              NaN         3.00 - 4.00   
2    Elektirk              NaN              3.50-3   
3     Sayısal              NaN              3.50-3   
4          TM              NaN         3.00 - 4.00   

  Baska Bir Kurumdan Burs Aliyor mu? Burs Aldigi Baska Kurum  \
0                              Hayır                     NaN   
1                              Hayır                     NaN   
2                              Hayır                     NaN   
3                              Hayır                     NaN   
4                              Hayır                     NaN   

  Baska Kurumdan Aldigi Burs Miktari Anne Egitim Durumu Anne Calisma Durumu  \
0                                NaN         Üniversite               Hayır   
1                                NaN         Üniversite                Evet   
2                                NaN     İlkokul Mezunu               Hayır   
3                                NaN     İlkokul Mezunu               Hayır   
4                                NaN     İlkokul Mezunu               Hayır   

  Anne Sektor       Baba Egitim Durumu Baba Calisma Durumu  Baba Sektor  \
0           0               Üniversite              Emekli            0   
1        Kamu  Yüksek Lisans / Doktora              Emekli            0   
2           0           İlkokul

In [3]:
df.isnull().sum().sort_values(ascending=True)

Basvuru Yili                                                     0
Burs Aliyor mu?                                                  0
id                                                               0
Degerlendirme Puani                                              1
Universite Adi                                                 132
Cinsiyet                                                       169
Dogum Tarihi                                                   177
Bölüm                                                          231
Baska Bir Kurumdan Burs Aliyor mu?                             231
Universite Turu                                                255
Universite Kacinci Sinif                                       374
Lise Adi                                                       384
Anne Egitim Durumu                                             406
Dogum Yeri                                                     791
Lise Turu                                                     

In [4]:
df = df.dropna(subset=['Degerlendirme Puani'])

In [5]:
def how_many_types(dataframe, col_name):
    
    diff_types = set(dataframe[col_name].apply(type))
    num_of_diff_types =len(diff_types)
    print(f"Sütunda {num_of_diff_types} farklı veri tipi var: {diff_types} ")

# Bütün harfleri küçük yapma
def all_letters_lowered(dataframe, col_name):
    """
    Belirtilen bir sütundaki tüm string değerleri küçük harfe çevirir.
    
    Parametreler:
    dataframe (pd.DataFrame): İşlem yapılacak DataFrame.
    col_name (str): Tüm string değerlerinin küçük harfe çevrileceği sütunun adı.
    
    İşlev:
    - Verilen sütundaki tüm string ifadeler `.str.lower()` ile küçük harfe dönüştürülür.
    
    Not:
    - Bu fonksiyon doğrudan orijinal DataFrame üzerinde değişiklik yapar (`inplace=True` gibi davranır).
    
    Örnek kullanım:
    all_letters_lowered(df, 'column_name')
    """
    dataframe[col_name] = dataframe[col_name].str.lower()


# Eşsiz değerleri ve NaN değerleri görme
def values_and_nulls(dataframe, col_name):
    """
    Belirtilen bir sütundaki eşsiz değerleri ve NaN değerlerinin sayısını gösterir.
    
    Parametreler:
    dataframe (pd.DataFrame): İşlem yapılacak DataFrame.
    col_name (str): Eşsiz değerlerin ve NaN değerlerinin sayısının hesaplanacağı sütun adı.
    
    İşlev:
    1. Sütundaki eşsiz değerleri ve bu değerlerin kaç kere tekrar ettiğini gösterir.
    2. Sütundaki NaN (eksik) değerlerin sayısını gösterir.
    
    Çıktı:
    - Sütundaki eşsiz değerlerin sıklığı.
    - NaN değerlerin sayısı.
    """
    print(dataframe[col_name].value_counts(), end="\n\n")
    print("NaN: ", dataframe[col_name].isnull().sum())

# NaN değerleri doldurma
def fill_missing_values(dataframe, col_name, value):
    """
    DataFrame'deki belirli bir sütundaki eksik (NaN) değerleri verilen değer ile doldurur.
    
    Parametreler:
    df (pd.DataFrame): İşlem yapılacak DataFrame.
    column (str): Eksik değerlerin doldurulacağı sütunun adı.
    value: Eksik değerlerin yerine yazılacak değer.
    """
    dataframe[col_name] = dataframe[col_name].fillna(value)

    

# CİNSİYET ✓

In [6]:
values_and_nulls(df, "Cinsiyet")

Cinsiyet
Kadın                    32076
Erkek                    22752
ERKEK                    10012
Belirtmek istemiyorum      115
Name: count, dtype: int64

NaN:  169


In [7]:
all_letters_lowered(df,"Cinsiyet")
fill_missing_values(df, "Cinsiyet", "Belirtmek istemiyorum")

In [8]:
mapping_sex = {"erkek": 1, "kadın": 2, "Belirtmek istemiyorum": 0}
df["Cinsiyet"] = df["Cinsiyet"].map(mapping_sex)
df["Cinsiyet"] = df["Cinsiyet"].fillna(0).astype(int)

In [9]:
values_and_nulls(df, "Cinsiyet")

Cinsiyet
1    32764
2    32076
0      284
Name: count, dtype: int64

NaN:  0


In [10]:
erkek_sayisi = len(df[df['Cinsiyet'] == 1])
kadin_sayisi = len(df[df['Cinsiyet'] == 2])
belirtmek_istemiyorum_sayisi = len(df[df['Cinsiyet'] == 0])

# Ağırlıklı dağıtım oranları
erkek_orani = erkek_sayisi / (erkek_sayisi + kadin_sayisi)
kadin_orani = kadin_sayisi / (erkek_sayisi + kadin_sayisi)

# Belirtmek istemiyorum'u cinsiyetlere dağıtma
erkek_eklenecek = int(belirtmek_istemiyorum_sayisi * erkek_orani)
kadin_eklenecek = belirtmek_istemiyorum_sayisi - erkek_eklenecek

# "Belirtmek İstemiyorum" olanları dağıtma
df.loc[df['Cinsiyet'] == 0, 'Cinsiyet'] = [1] * erkek_eklenecek + [2] * kadin_eklenecek

In [11]:
values_and_nulls(df, "Cinsiyet")

Cinsiyet
1    32907
2    32217
Name: count, dtype: int64

NaN:  0


# DOĞUM TARİHİ

In [12]:
values_and_nulls(df, "Dogum Tarihi")

Dogum Tarihi
1/1/70 2:00            1655
1/1/00 0:00             179
1/1/01 0:00             154
1/1/1997                139
1/1/1998                129
1/1/1996                119
1/1/99 0:00             117
1/1/1995                106
1/1/1999                 84
1.01.2001 00:00          82
1/1/98 0:00              81
1-Jan-95                 78
1/1/1994                 73
1/1/02 0:00              71
1/1/1993                 68
1.01.2000 00:00          61
1-Jan-94                 59
1.01.2002 00:00          59
1-Jan-90                 57
1-Jan-96                 52
1/1/2000                 50
1-Jan-93                 43
1/1/97 0:00              43
1994-01-01               40
1/1/1970                 38
1/1/1992                 37
1995-01-01               36
1996-01-01               35
1/1/1991                 32
10/1/1997                30
1.01.1999 00:00          29
3/1/00 0:00              29
9/15/99 0:00             27
1/2/1997                 27
3/1/1997                 27
1/3/00 

In [13]:
df['Dogum Tarihi'] = pd.to_datetime(df['Dogum Tarihi'], errors='coerce', dayfirst=True)

In [14]:
values_and_nulls(df,"Dogum Tarihi")

Dogum Tarihi
1997-01-01    139
1998-01-01    129
1996-01-01    119
1995-01-01    106
1999-01-01     84
1994-01-01     73
1993-01-01     68
2000-01-01     50
1970-01-01     38
1992-01-01     37
1991-01-01     32
1997-01-10     30
1997-02-01     27
1997-01-03     27
1997-05-05     26
1997-01-08     25
1996-01-11     24
1998-02-02     23
1997-01-02     23
1995-02-02     22
1998-02-01     22
1998-12-01     22
1998-05-05     21
1997-10-10     21
1996-01-10     21
1998-04-01     21
1998-08-05     20
1996-01-08     20
1998-01-04     20
1998-01-10     20
1996-01-07     20
1997-09-05     20
1997-07-07     19
1997-06-06     19
1997-04-01     19
1999-01-10     19
1995-03-01     19
1998-10-10     19
1996-06-06     19
1997-01-07     19
1997-03-10     19
1995-02-01     19
1998-10-02     18
1998-07-01     18
1998-06-01     18
1998-01-05     18
1997-10-07     18
1997-04-08     18
1997-01-04     18
1995-10-10     18
1996-01-04     18
1997-05-06     18
1998-10-01     18
1993-01-07     17
1999-09-09     

# Dogum Yeri, İkametgah Sehri, Lise Sehir ✓

In [15]:
df_ilce = pd.read_csv("il_ilce.csv")
values_and_nulls(df,"Dogum Yeri")
fill_missing_values(df,"Dogum Yeri", "Diğer")
fill_missing_values(df,"Lise Sehir", "Diğer")
fill_missing_values(df,"Ikametgah Sehri", "Diğer")

Dogum Yeri
İstanbul                                                         8682
Ankara                                                           4045
İzmir                                                            2170
Istanbul                                                         1894
Adana                                                            1810
Bursa                                                            1809
Mersin                                                           1447
Konya                                                            1436
Diyarbakır                                                       1377
Hatay                                                            1325
Gaziantep                                                        1310
Antalya                                                          1174
Kayseri                                                          1141
Van                                                              1099
Şanlıurfa

In [16]:
from unidecode import unidecode

def clean_city(df, df_ilce):
    # Türkçe karakterleri ASCII karşılıklarına çeviren yardımcı fonksiyon
    def normalize_str(s):
        # Convert the input to uppercase to handle cases like "i" vs "İ"
        normalized = unidecode(s).upper()
        # Replace specific cases manually to handle exceptions
        replacements = {'I': 'I', 'İ': 'I', 'Ş': 'S', 'Ç': 'C', 'Ö': 'O', 'Ü': 'U', 'Ğ': 'G'}
        for turkish_char, ascii_char in replacements.items():
            normalized = normalized.replace(turkish_char, ascii_char)
        return normalized

    # İl ve ilçe isimlerini normalize edelim
    df_ilce['il_norm'] = df_ilce['il'].apply(normalize_str)
    df_ilce['ilce_norm'] = df_ilce['ilce'].apply(normalize_str)

    # İl-ilçe eşleşmelerini bir sözlükte saklayalım
    ilce_il_dict = dict(zip(df_ilce['ilce_norm'], df_ilce['il']))

    def update_city(dogum_yeri):
        dogum_yeri_norm = normalize_str(dogum_yeri)

        # Eğer girdi doğrudan bir il ise, olduğu gibi döndür
        if dogum_yeri_norm in df_ilce['il_norm'].values:
            return df_ilce.loc[df_ilce['il_norm'] == dogum_yeri_norm, 'il'].iloc[0]

        # Eğer girdi bir ilçe ise, ilini bul
        elif dogum_yeri_norm in ilce_il_dict:
            return ilce_il_dict[dogum_yeri_norm]

        # Eğer girdi hem il hem ilçe içeriyorsa, il kısmını al
        else:
            for il_norm in df_ilce['il_norm'].unique():
                if il_norm in dogum_yeri_norm:
                    return df_ilce.loc[df_ilce['il_norm'] == il_norm, 'il'].iloc[0]

        # Hiçbiri değilse "DİĞER" olarak işaretle
        return "Diğer"

    # Dogum Yeri sütununu güncelle
    df['Dogum Yeri'] = df['Dogum Yeri'].apply(update_city)
    df['Lise Sehir'] = df['Lise Sehir'].apply(update_city)
    df['Ikametgah Sehri'] = df['Ikametgah Sehri'].apply(update_city)

    return df

cities = ['adana', 'adıyaman', 'afyonkarahisar', 'ağrı', 'amasya', 'ankara', 'antalya', 'artvin',
                    'aydın', 'balıkesir', 'bilecik',  'bingöl', 'bitlis', 'bolu', 'burdur', 'bursa', 'çanakkale',
                    'çankırı', 'çorum', 'denizli', 'diyarbakır', 'edirne', 'elazığ',  'erzincan', 'erzurum', 'eskişehir',
                    'gaziantep', 'giresun', 'gümüşhane', 'hakkari', 'hatay', 'isparta', 'mersin', 'i̇stanbul',  'i̇zmir',
                    'kars', 'kastamonu', 'kayseri', 'kırklareli', 'kırşehir', 'kocaeli', 'konya', 'kütahya', 'malatya',
                    'manisa',  'kahramanmaraş', 'mardin', 'muğla', 'muş', 'nevşehir', 'niğde', 'ordu', 'rize', 'sakarya',
                    'samsun', 'siirt', 'sinop', 'sivas',  'tekirdağ', 'tokat', 'trabzon', 'tunceli', 'şanlıurfa', 'uşak',
                    'van', 'yozgat', 'zonguldak', 'aksaray', 'bayburt', 'karaman',  'kırıkkale', 'batman', 'şırnak', 'bartın',
                    'ardahan', 'iğdır', 'yalova', 'karabük', 'kilis', 'osmaniye', 'düzce']

all_letters_lowered(df,"Dogum Yeri")
all_letters_lowered(df_ilce,"il")
all_letters_lowered(df_ilce,"ilce")

def clean_city(df,df_ilce,col_name):
    df = df.merge(df_ilce, left_on=col_name, right_on='ilce', how='left')
    df[col_name] = df.apply(lambda row: row['il'] if pd.notnull(row['il']) else row[col_name], axis=1)
    df = df.drop(['ilce', 'il'], axis=1)
    df[col_name] = df[col_name].apply(lambda x: x if x in cities else "diğer")

clean_city(df, df_ilce, "Dogum Yeri")
clean_city(df, df_ilce, "Ikametgah Sehri")
clean_city(df, df_ilce, "Lise Sehir")

In [17]:
clean_city(df,df_ilce)

values_and_nulls(df,"Dogum Yeri")
values_and_nulls(df,"Lise Sehir")
values_and_nulls(df,"Ikametgah Sehri")

Dogum Yeri
İstanbul          11482
Ankara             4389
İzmir              2968
Bursa              1976
Adana              1948
Diğer              1827
Diyarbakır         1667
Konya              1541
Mersin             1528
Hatay              1432
Gaziantep          1377
Şanlıurfa          1323
Antalya            1246
Kayseri            1214
Van                1145
Kocaeli            1060
Mardin             1026
Malatya             983
Samsun              973
Erzurum             950
Manisa              918
Kahramanmaraş       807
Balıkesir           779
Denizli             748
Ağrı                722
Eskişehir           682
Aydın               676
Adıyaman            675
Sivas               669
Trabzon             662
Batman              629
Ordu                593
Elazığ              551
Tokat               550
Sakarya             549
Çorum               519
Tekirdağ            511
Muş                 475
Zonguldak           471
Muğla               466
Şırnak              456
Yozga

# Üniversite Adı ✓

In [18]:
values_and_nulls(df,"Universite Adi")

Universite Adi
İSTANBUL ÜNİVERSİTESİ                                       2083
MARMARA ÜNİVERSİTESİ                                        1672
İSTANBUL TEKNİK ÜNİVERSİTESİ                                1464
YILDIZ TEKNİK ÜNİVERSİTESİ                                  1438
ORTA DOĞU TEKNİK ÜNİVERSİTESİ                               1258
DOKUZ EYLÜL ÜNİVERSİTESİ                                    1235
BOĞAZİÇİ ÜNİVERSİTESİ                                       1165
KOCAELİ ÜNİVERSİTESİ                                        1004
HACETTEPE ÜNİVERSİTESİ                                       938
GAZİ ÜNİVERSİTESİ                                            910
EGE ÜNİVERSİTESİ                                             887
SELÇUK ÜNİVERSİTESİ                                          886
ANADOLU ÜNİVERSİTESİ                                         853
ANKARA ÜNİVERSİTESİ                                          833
SAKARYA ÜNİVERSİTESİ                                         803
AKDENİZ ÜN

In [19]:

fill_missing_values(df,"Universite Adi","diger")

In [20]:
import unidecode

def standardize_name(name):
    name = name.strip()  # Başındaki ve sonundaki boşlukları kaldır
    name = ' '.join(name.split())  # Aralardaki fazla boşlukları tek boşlukla değiştir
    name = name.lower()  # Küçük harfe dönüştür
    name = unidecode.unidecode(name)  # Türkçe karakterleri İngilizce karakterlere dönüştür
    return name

# Uygulama
df['Universite Adi'] = df['Universite Adi'].apply(standardize_name)

In [21]:
# BURADAKİ 100 SAYISI MODELDEN SONRA DEĞİŞTİRİLİP TEKRAR DENENEBİLİR

uni_counts = df['Universite Adi'].value_counts()
values_to_update = uni_counts[uni_counts < 10].index
df['Universite Adi'] = df['Universite Adi'].apply(lambda x: 'diger' if x in values_to_update else x)

In [22]:
values_and_nulls(df,"Universite Adi")

Universite Adi
istanbul universitesi                                     2572
marmara universitesi                                      2084
istanbul teknik universitesi                              1954
yildiz teknik universitesi                                1916
orta dogu teknik universitesi                             1658
bogazici universitesi                                     1572
dokuz eylul universitesi                                  1495
kocaeli universitesi                                      1237
hacettepe universitesi                                    1215
ege universitesi                                          1102
gazi universitesi                                         1087
selcuk universitesi                                       1055
ankara universitesi                                       1033
anadolu universitesi                                       991
sakarya universitesi                                       967
akdeniz universitesi                    

# Üniversite Türü  ✓

In [23]:
all_letters_lowered(df,"Universite Turu")
fill_missing_values(df,"Universite Turu" , "devlet") # burası modelden sonra oynanabilir.
values_and_nulls(df, "Universite Turu")


Universite Turu
devlet    53516
özel      11608
Name: count, dtype: int64

NaN:  0


# Burslu ise Burs Yuzdesi ✓

In [24]:
fill_missing_values(df,"Burslu ise Burs Yuzdesi",0)
values_and_nulls(df, "Burslu ise Burs Yuzdesi")

Burslu ise Burs Yuzdesi
0.0      54856
100.0     5049
50.0      3149
75.0      1002
25.0       785
10.0        50
60.0        27
1.0         26
65.0        17
80.0        15
5.0         14
30.0        14
85.0        11
2.0         10
55.0         8
62.5         7
62.0         7
35.0         7
45.0         6
7.0          6
70.0         5
99.0         5
20.0         5
40.0         4
90.0         4
63.0         4
6.0          4
3.0          2
8.0          2
98.0         2
46.0         1
82.5         1
69.0         1
88.0         1
64.0         1
4.0          1
87.5         1
57.5         1
57.0         1
91.5         1
11.0         1
41.5         1
49.0         1
74.0         1
72.0         1
32.0         1
48.0         1
37.0         1
67.0         1
41.0         1
67.5         1
Name: count, dtype: int64

NaN:  0


In [25]:
bins = [-1, 10, 20, 30, 40, 50, 60, 70, 80, 90, 100]
labels = ['0-10', '11-20', '21-30', '31-40', '41-50', '51-60', '61-70', '71-80', '81-90', '91-100']

df['Burslu ise Burs Yuzdesi'] = pd.cut(df['Burslu ise Burs Yuzdesi'], bins=bins, labels=labels, right=True)

In [26]:
values_and_nulls(df,"Burslu ise Burs Yuzdesi")

Burslu ise Burs Yuzdesi
0-10      54971
91-100     5057
41-50      3160
71-80      1019
21-30       799
61-70        44
51-60        37
81-90        18
31-40        13
11-20         6
Name: count, dtype: int64

NaN:  0


# Burs Aliyor mu? ✓

In [27]:
all_letters_lowered(df, "Burs Aliyor mu?")

In [28]:
values_and_nulls(df,"Burs Aliyor mu?")

Burs Aliyor mu?
hayır    52249
evet     12875
Name: count, dtype: int64

NaN:  0


# Bölüm ✓

In [29]:
values_and_nulls(df,"Bölüm")
fill_missing_values(df,"Bölüm","diger")

Bölüm
Endüstri Mühendisliği                                                                                                                                                                                                                                       2434
İşletme                                                                                                                                                                                                                                                     2318
Bilgisayar Mühendisliği                                                                                                                                                                                                                                     1917
Hukuk                                                                                                                                                                                                                          

In [30]:
df["Bölüm"] = df["Bölüm"].apply(standardize_name)

In [31]:
department_counts = df["Bölüm"].value_counts()
values_to_update = department_counts[department_counts < 10].index
df["Bölüm"] = df["Bölüm"].apply(lambda x: 'diger' if x in values_to_update else x)

In [32]:
values_and_nulls(df,"Bölüm")

Bölüm
diger                                                                     9228
isletme                                                                   2913
endustri muhendisligi                                                     2835
bilgisayar muhendisligi                                                   2245
hukuk                                                                     2007
makine muhendisligi                                                       1552
iktisat                                                                   1529
tip                                                                       1334
insaat muhendisligi                                                       1206
uluslararasi iliskiler                                                     974
elektrik-elektronik muhendisligi                                           957
elektrik elektronik muhendisligi                                           830
mimarlik                                      

# Universite Kacinci Sinif ✓

In [33]:
values_and_nulls(df, "Universite Kacinci Sinif")

Universite Kacinci Sinif
2                21773
3                16956
4                13112
1                10260
Hazırlık          1275
5                  961
Mezun              178
6                  177
hazırlık            33
Yüksek Lisans       15
Tez                  7
0                    3
Name: count, dtype: int64

NaN:  374


In [34]:
all_letters_lowered(df,"Universite Kacinci Sinif")

In [35]:
values_and_nulls(df,"Universite Kacinci Sinif")

Universite Kacinci Sinif
2                21773
3                16956
4                13112
1                10260
hazırlık          1308
5                  961
mezun              178
6                  177
yüksek lisans       15
tez                  7
0                    3
Name: count, dtype: int64

NaN:  374


In [36]:
# Mod ile doldurdum.
mode_value = df['Universite Kacinci Sinif'].mode()[0]
fill_missing_values(df,"Universite Kacinci Sinif", mode_value)
values_and_nulls(df,"Universite Kacinci Sinif")

Universite Kacinci Sinif
2                22147
3                16956
4                13112
1                10260
hazırlık          1308
5                  961
mezun              178
6                  177
yüksek lisans       15
tez                  7
0                    3
Name: count, dtype: int64

NaN:  0


In [37]:
how_many_types(df,"Universite Kacinci Sinif")

Sütunda 1 farklı veri tipi var: {<class 'str'>} 


In [38]:
grades = {
    '0': 7,
    '1' : 1,
    '2': 2,
    '3':3,
    '4':4,
    '5':5,
    '6':6,
    'hazırlık': 0,
    'mezun': 7,
    'yüksek lisans': 8,
    'tez': 9
}

df['Universite Kacinci Sinif'] = df['Universite Kacinci Sinif'].map(grades)

In [39]:
how_many_types(df,"Universite Kacinci Sinif")

Sütunda 1 farklı veri tipi var: {<class 'int'>} 


In [40]:
df["Universite Kacinci Sinif"].nunique()

10

In [41]:
values_and_nulls(df,"Universite Kacinci Sinif")

Universite Kacinci Sinif
2    22147
3    16956
4    13112
1    10260
0     1308
5      961
7      181
6      177
8       15
9        7
Name: count, dtype: int64

NaN:  0


# Universite Not Ortalamasi ✓

In [42]:
all_letters_lowered(df,"Universite Not Ortalamasi")
values_and_nulls(df,"Universite Not Ortalamasi")

Universite Not Ortalamasi
3.00-2.50              10758
2.50 ve altı           10554
3.00 - 3.50             7913
3.50-3                  6179
2.50 - 3.00             5782
3.50 - 4.00             4462
ortalama bulunmuyor     2812
2.00 - 2.50             2519
2.50 - 2.99             2451
3.00 - 3.49             2382
2.50 -3.00              1734
3.00 - 4.00             1411
1.80 - 2.49             1166
hazırlığım               668
not ortalaması yok       586
4-3.5                    481
1.00 - 2.50              327
0 - 1.79                 185
4.0-3.5                    1
Name: count, dtype: int64

NaN:  2753


In [43]:
how_many_types(df,"Universite Not Ortalamasi")

Sütunda 2 farklı veri tipi var: {<class 'float'>, <class 'str'>} 


In [44]:
fill_missing_values(df,"Universite Not Ortalamasi","yok")

In [45]:
how_many_types(df,"Universite Not Ortalamasi")

Sütunda 1 farklı veri tipi var: {<class 'str'>} 


In [46]:
values_and_nulls(df,"Universite Not Ortalamasi")

Universite Not Ortalamasi
3.00-2.50              10758
2.50 ve altı           10554
3.00 - 3.50             7913
3.50-3                  6179
2.50 - 3.00             5782
3.50 - 4.00             4462
ortalama bulunmuyor     2812
yok                     2753
2.00 - 2.50             2519
2.50 - 2.99             2451
3.00 - 3.49             2382
2.50 -3.00              1734
3.00 - 4.00             1411
1.80 - 2.49             1166
hazırlığım               668
not ortalaması yok       586
4-3.5                    481
1.00 - 2.50              327
0 - 1.79                 185
4.0-3.5                    1
Name: count, dtype: int64

NaN:  0


In [47]:
gpa = {
    '3.50-3': 'iyi',
    '3.00-2.50': 'iyi',
    'yok': 'yok',
    '2.50 ve altı': 'kotu',
    '3.00 - 4.00': 'iyi',
    '3.50 - 4.00': 'harika',
    '3.00 - 3.50': 'iyi',
    '2.50 -3.00': 'iyi',
    'ortalama bulunmuyor': 'yok',
    '4-3.5': 'harika',
    '2.50 - 3.00': 'kotu',
    '2.00 - 2.50': 'kotu',
    '1.00 - 2.50': 'kotu',
    'not ortalaması yok': 'yok',
    '4.0-3.5':'harika',
    '3.00 - 3.49':  'iyi',
    '2.50 - 2.99':  'iyi',
    '1.80 - 2.49': 'kotu',
    'hazırlığım': 'yok',
    '0 - 1.79': 'kotu'
}
df['Universite Not Ortalamasi'] = df['Universite Not Ortalamasi'].map(gpa)

In [48]:
values_and_nulls(df,"Universite Not Ortalamasi")

Universite Not Ortalamasi
iyi       32828
kotu      20533
yok        6819
harika     4944
Name: count, dtype: int64

NaN:  0


# Daha Once Baska Bir Universiteden Mezun Olmus ✓

In [49]:
all_letters_lowered(df,"Daha Once Baska Bir Universiteden Mezun Olmus")
values_and_nulls(df,"Daha Once Baska Bir Universiteden Mezun Olmus")

Daha Once Baska Bir Universiteden Mezun Olmus
hayır    26624
evet      1156
Name: count, dtype: int64

NaN:  37344


In [50]:
fill_missing_values(df,"Daha Once Baska Bir Universiteden Mezun Olmus","hayır")
values_and_nulls(df,"Daha Once Baska Bir Universiteden Mezun Olmus")

Daha Once Baska Bir Universiteden Mezun Olmus
hayır    63968
evet      1156
Name: count, dtype: int64

NaN:  0


# Lise Adi ✓

In [51]:
values_and_nulls(df,"Lise Adi")

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [52]:
all_letters_lowered(df,"Lise Adi")
def name_highschool(df, column_name):
    df.loc[df[column_name].str.contains('anadolu', case=False, na=False), column_name] = 'anadolu'
    df.loc[df[column_name].str.contains('fen', case=False, na=False), column_name] = 'fen'
    df.loc[
        (df[column_name].str.contains('meslek', case=False, na=False)) |
        (df[column_name].str.contains('ticar', case=False, na=False)) ,
        column_name
    ] = 'meslek'
    df.loc[df[column_name].str.contains('atatürk', case=False, na=False), column_name] = 'atatürk'
    
    hs = {
    'anadolu': 1,
    'fen': 2,
    'meslek': 3,
    'atatürk': 4,
    }
    
    df[column_name] = df[column_name].map(hs)



In [53]:
name_highschool(df,"Lise Adi")

fill_missing_values(df,"Lise Adi","diğer")
df['Lise Adi'] = df['Lise Adi'].replace('diğer', 0)
values_and_nulls(df,"Lise Adi")


Lise Adi
1.0    35889
0.0    21375
2.0     5442
3.0     1788
4.0      630
Name: count, dtype: int64

NaN:  0


# Lise Türü ✓

In [54]:
values_and_nulls(df,"Lise Turu")

Lise Turu
Anadolu Lisesi       13367
Diğer                13184
Anadolu lisesi        7002
Devlet                6203
Özel                  4746
Düz lise              4179
Meslek lisesi         3666
Düz Lise              2789
Meslek                2454
Fen Lisesi            2159
Özel Lisesi           1474
İmam Hatip Lisesi     1158
Fen lisesi             660
Özel lisesi            489
Meslek Lisesi          415
Özel Lise              332
Name: count, dtype: int64

NaN:  847


In [55]:
def kind_highschool(df, column_name):
    df.loc[df[column_name].str.contains('anadolu', case=False, na=False), column_name] = 'anadolu'
    df.loc[df[column_name].str.contains('fen', case=False, na=False), column_name] = 'fen'
    df.loc[(df[column_name].str.contains('meslek', case=False, na=False)) ,column_name] = 'meslek'
    df.loc[df[column_name].str.contains('özel', case=False, na=False), column_name] = 'özel'
    df.loc[df[column_name].str.contains('imam', case=False, na=False), column_name] = 'imam hatip'
    df.loc[df[column_name].str.contains('düz', case=False, na=False), column_name] = 'düz'
    df.loc[df[column_name].str.contains('diğer', case=False, na=False), column_name] = 'diğer'
    df.loc[df[column_name].str.contains('devlet', case=False, na=False), column_name] = 'devlet'
    
    hs = {
    'anadolu': 1,
    'fen': 2,
    'meslek': 3,
    'özel': 4,
    'imam hatip':5,
    'düz':6,
    'devlet':7,
    'diğer':0
    }
    
    df[column_name] = df[column_name].map(hs)

In [56]:
fill_missing_values(df,"Lise Turu","diğer")
kind_highschool(df,"Lise Turu")

In [57]:
values_and_nulls(df,"Lise Turu")

Lise Turu
1    20369
0    14031
4     7041
6     6968
3     6535
7     6203
2     2819
5     1158
Name: count, dtype: int64

NaN:  0


# Lise Bolumu ✓

In [58]:
values_and_nulls(df,"Lise Bolumu")

Lise Bolumu
Sayısal                                                                                                                                                                                 28980
Eşit Ağırlık                                                                                                                                                                            16936
FEN SAYISAL BİLİMLERİ ALANI                                                                                                                                                              3995
Sözel                                                                                                                                                                                    3630
EŞİT AĞIRLIK TÜRKÇE-MATEMATİK ALANI                                                                                                                                                      2786
Dil                                   

In [59]:
fill_missing_values(df,"Bölüm","diger")
df["Lise Bolumu"] = df["Lise Bolumu"].apply(lambda x: "diger" if isinstance(x, float) else x)
df["Lise Bolumu"]

0                                                       MF
1                                                       MF
2                                                 Elektirk
3                                                  Sayısal
4                                                       TM
5                                                       EA
6                                                  Sayısal
7                                                  Sayısal
8                                                   TS 1-2
9                                                      Fen
10                                                Düz lise
11                                                 sayısal
12                                                 Sayısal
13                                  Elektrikli Ev Aletleri
14                                            EŞIT AĞIRLIK
15                                                     Fen
16                                                 Sayıs

In [ ]:
import re
import unicodedata
def normalize_text(text):
    # Küçük harfe çevir
    text = text.lower()

    # Türkçe karakterleri İngilizce karakterlere dönüştür
    replacements = {
        'ç': 'c', 'ğ': 'g', 'ı': 'i', 'ö': 'o', 'ş': 's', 'ü': 'u'
    }
    for turkish_char, english_char in replacements.items():
        text = text.replace(turkish_char, english_char)
    
    # Unicode normalizasyonu yaparak özel karakterleri temizle
    text = unicodedata.normalize('NFKD', text)
    text = ''.join([c for c in text if not unicodedata.combining(c)])

    # Özel karakterleri sil (sadece harfler ve sayılar kalsın)
    text = re.sub(r'[^a-zA-Z0-9\s]', '', text)

    return text

# Veri setindeki bir sütuna uygulamak için
def normalize_column(df, column_name):
    df[column_name] = df[column_name].apply(normalize_text)
    return df
normalize_column(df,"Lise Bolumu")

In [ ]:
belirli_bolumler = ["sayısal", "dil", "eşit ağırlık","sözel"]
df['Lise Bolumu'] = df['Lise Bolumu'].apply(lambda x: x if x in belirli_bolumler else "diger")

In [ ]:
values_and_nulls(df,"Lise Bolumu")

# Lise Mezuniyet Notu ✓

In [ ]:
values_and_nulls(df,"Lise Mezuniyet Notu")
fill_missing_values(df,"Lise Mezuniyet Notu",0)
df["Lise Mezuniyet Notu"] = df["Lise Mezuniyet Notu"].replace('Not ortalaması yok', 0)

In [ ]:
highs_grades = {
    '75 - 100': 'A+',
    '84-70': 'B',
    '100-85': 'A+',
    '0':'C',
    '4.00-3.50': 'A+',
    '50 - 75': 'A',
    '3.00 - 4.00': 'B',
    '3.50-3.00': 'B',
    '3.50-3': 'B',
    '69-55': 'A',
    '3.00-2.50': 'A',
    '50 - 74': 'A',
    '2.50 ve altı': 'A',
    '54-45': 'C',
    '25 - 50': 'C',
    '44-0': 'C',
    '0 - 25': 'C',
    '25 - 49': 'C',
    '0 - 24': 'C',
    0: 'C'
}
df["Lise Mezuniyet Notu"] = df["Lise Mezuniyet Notu"].map(highs_grades)

In [ ]:
values_and_nulls(df,"Lise Mezuniyet Notu")

# Baska Bir Kurumdan Burs Aliyor mu? ✓

In [ ]:
all_letters_lowered(df,"Baska Bir Kurumdan Burs Aliyor mu?")
values_and_nulls(df,"Baska Bir Kurumdan Burs Aliyor mu?")

In [ ]:
fill_missing_values(df,"Baska Bir Kurumdan Burs Aliyor mu?","hayır")
values_and_nulls(df,"Baska Bir Kurumdan Burs Aliyor mu?")

# Burs Aldigi Baska Kurum BİTMEDİ!!!!

In [ ]:
all_letters_lowered(df,"Burs Aldigi Baska Kurum")
values_and_nulls(df,"Burs Aldigi Baska Kurum")

In [ ]:
def sade(df, col_name, word_map):
    # Sütundaki her satırı kontrol et
    def replace_word(text):
        standardized_text = standardize_name(text)
        # Her kelime listesi için kontrol et
        for target_word, word_list in word_map.items():
            if any(word in standardized_text for word in word_list):
                return target_word
        return standardized_text

    df[col_name] = df[col_name].apply(replace_word)
    
    

In [ ]:
df['Burs Aldigi Baska Kurum'] = df['Burs Aldigi Baska Kurum'].apply(lambda x: "almiyor" if isinstance(x, float) else x)

In [ ]:
scholar_list = {
                "kyk" : ["kyk","kredi","yurtlar","ky",],
                "tev" : ["tev","türk eğitim vakfı","turk eğitim vakfı"],
                "devlet" : ["devlet"],
                "gsb": ["gsb","genclik ve spor bakanligi"],
                "vgm" : ["vgm","vakiflar genel mudurlugu"],
                "almiyor": ["almiyorum","hayir"]
                }

sade(df,"Burs Aldigi Baska Kurum",scholar_list)


KYK, kyk, Kyk gibi farklı türevleri hızlıca birleştirmek için hepsini küçük karakter yapıyoruz. Diğer bazı sütunlarda da böyle.
all_letters_lowered(df,"Burs Aldigi Baska Kurum")
values_and_nulls(df,"Burs Aldigi Baska Kurum")

In [ ]:
values_and_nulls(df,"Burs Aldigi Baska Kurum")

In [ ]:
value_counts = df['Burs Aldigi Baska Kurum'].value_counts()
values_to_update = value_counts[value_counts < 10].index
df['Burs Aldigi Baska Kurum'] = df['Burs Aldigi Baska Kurum'].apply(lambda x: 'diğer' if x in values_to_update else x)

# Anne Egitim Durumu & Baba Egitim Durumu ✓

In [ ]:
def update_edu(df, column_name):
    df.loc[df[column_name].str.contains('ilkokul', case=False, na=False), column_name] = 'ilkokul'
    df.loc[df[column_name].str.contains('lise', case=False, na=False), column_name] = 'lise'
    df.loc[df[column_name].str.contains('üniversite', case=False, na=False), column_name] = 'üniversite'
    df.loc[df[column_name].str.contains('doktora', case=False, na=False), column_name] = 'doktora'
    df.loc[df[column_name].str.contains('yüksek', case=False, na=False), column_name] = 'yüksek lisans'
    df.loc[df[column_name].str.contains('ortaokul', case=False, na=False), column_name] = 'ortaokul'
    df.loc[
        (df[column_name].str.contains('0', case=False, na=False)) |
        (df[column_name].str.contains('eğitimi yok', case=False, na=False)) |
        (df[column_name].str.contains('eğitim yok', case=False, na=False)),
        column_name
    ] = 'yok'
    
    _edu = {
    'ilkokul': 1,
    'ortaokul': 2,
    'lise': 3,
    'üniversite': 4,
    'yüksek lisans': 5,
    'doktora': 6,
    'yok': 0
    }
    fill_missing_values(df,column_name,"yok")
    df[column_name] = df[column_name].map(_edu)
    

In [ ]:
update_edu(df,"Anne Egitim Durumu")
update_edu(df,"Baba Egitim Durumu")

# Anne Çalışma Durumu & Baba Çalışma Durumu ✓

In [ ]:
fill_missing_values(df,"Anne Calisma Durumu","yok")
fill_missing_values(df,"Baba Calisma Durumu","yok")

In [ ]:
work = {
    'Hayır': 1,
    'Evet': 2,
    'Emekli': 3,
    'yok': 0,
    }
df["Baba Calisma Durumu"] = df["Baba Calisma Durumu"].map(work)
df["Anne Calisma Durumu"] = df["Anne Calisma Durumu"].map(work)

In [ ]:
values_and_nulls(df,"Anne Calisma Durumu")
values_and_nulls(df,"Baba Calisma Durumu")

# Anne Sektor & Baba Sektor ✓

In [ ]:
def update_sector(df, column_name):
    df.loc[df[column_name].str.contains('özel', case=False, na=False), column_name] = 'özel'
    df.loc[df[column_name].str.contains('kamu', case=False, na=False), column_name] = 'kamu'
    df.loc[df[column_name].str.contains('diğer', case=False, na=False), column_name] = 'diğer'
    df.loc[
        (df[column_name].str.contains('0', case=False, na=False)) |
        (df[column_name].str.contains('-', case=False, na=False)) ,
        column_name
    ] = 'yok'
    
    sector = {
    'kamu': 1,
    'özel': 2,
    'diğer': 3,
    'yok': 0,
    }
    fill_missing_values(df,column_name,"yok")
    df[column_name] = df[column_name].map(sector)

In [ ]:
update_sector(df,"Baba Sektor")
update_sector(df,"Anne Sektor")

# Kardes Sayisi ✓

In [ ]:
values_and_nulls(df,"Kardes Sayisi")
how_many_types(df,"Kardes Sayisi")
df['Kardes Sayisi'] = df['Kardes Sayisi'].replace('Kardeş Sayısı 1 Ek Bilgi Aile Hk. Anne Vefat', 1)
fill_missing_values(df,"Kardes Sayisi",0)
df['Kardes Sayisi'] = df['Kardes Sayisi'].astype(int)

In [ ]:
# 6 ve 6dan fazlaları bir araya getirdim.
df['Kardes Sayisi'] = df['Kardes Sayisi'].apply(lambda x: 6 if x >= 6 else x)
values_and_nulls(df,"Kardes Sayisi")

# Girisimcilik Kulupleri Tarzi Bir Kulube Uye misiniz? ✓

In [ ]:
values_and_nulls(df,"Girisimcilik Kulupleri Tarzi Bir Kulube Uye misiniz?")

In [ ]:
fill_missing_values(df,"Girisimcilik Kulupleri Tarzi Bir Kulube Uye misiniz?","Hayır")

# Uye Oldugunuz Kulubun Ismi SONRA BAKICAM !!!!!!!!!!!!!!!!!!!!! 

# Profesyonel Bir Spor Daliyla Mesgul musunuz? ✓

In [ ]:
values_and_nulls(df,"Profesyonel Bir Spor Daliyla Mesgul musunuz?")

In [ ]:
fill_missing_values(df,"Profesyonel Bir Spor Daliyla Mesgul musunuz?","Hayır")

# Spor Dalindaki Rolunuz Nedir BİDAHA BAK !!!!!!!!!

In [ ]:
values_and_nulls(df,"Spor Dalindaki Rolunuz Nedir?")

In [ ]:
def update_sport_role(df, column_name):
    df.loc[
        (df[column_name].str.contains('diğer', case=False, na=False)) |
        (df[column_name].str.contains('takim oyuncusu', case=False, na=False)), column_name] = 'diğer'
    
    df.loc[df[column_name].str.contains('lider', case=False, na=False), column_name] = 'lider'
    df.loc[df[column_name].str.contains('bireysel', case=False, na=False), column_name] = 'bireysel'
    
    df.loc[
        (df[column_name].str.contains('0', case=False, na=False)) |
        (df[column_name].str.contains('-', case=False, na=False)) ,
        column_name
    ] = 'yok'
    
    role = {
    'lider': 1,
    'bireysel': 2,
    'diğer': 3,
    'yok': 0,
    }
    fill_missing_values(df,column_name,"yok")
    df[column_name] = df[column_name].map(role)

In [ ]:
update_sport_role(df,"Spor Dalindaki Rolunuz Nedir?")
values_and_nulls(df,"Spor Dalindaki Rolunuz Nedir?")
fill_missing_values(df,"Spor Dalindaki Rolunuz Nedir?",0)

# Aktif olarak bir STK üyesi misiniz? ✓

In [ ]:
values_and_nulls(df,"Aktif olarak bir STK üyesi misiniz?")

In [ ]:
fill_missing_values(df,"Aktif olarak bir STK üyesi misiniz?","Hayır")

In [ ]:
values_and_nulls(df,"Aktif olarak bir STK üyesi misiniz?")

# Hangi STK'nin Uyesisiniz?

# Stk Projesine Katildiniz Mi? ✓

In [ ]:
values_and_nulls(df,"Stk Projesine Katildiniz Mi?")

In [ ]:
fill_missing_values(df,"Stk Projesine Katildiniz Mi?","Hayır")

In [ ]:
values_and_nulls(df,"Stk Projesine Katildiniz Mi?")

# Girisimcilikle Ilgili Deneyiminiz Var Mi? ✓

In [ ]:
values_and_nulls(df,"Girisimcilikle Ilgili Deneyiminiz Var Mi?")

In [ ]:
fill_missing_values(df,"Girisimcilikle Ilgili Deneyiminiz Var Mi?","Hayır")

In [ ]:
values_and_nulls(df,"Girisimcilikle Ilgili Deneyiminiz Var Mi?")

# Girisimcilikle Ilgili Deneyiminizi Aciklayabilir misiniz?

# Ingilizce Biliyor musunuz? ✓

In [ ]:
values_and_nulls(df,"Ingilizce Biliyor musunuz?")

In [ ]:
fill_missing_values(df,"Ingilizce Biliyor musunuz?","Hayır")

In [ ]:
values_and_nulls(df,"Ingilizce Biliyor musunuz?")

# Ingilizce Seviyeniz? ✓

In [ ]:
values_and_nulls(df,"Ingilizce Seviyeniz?")

In [ ]:
fill_missing_values(df,"Ingilizce Seviyeniz?","0")

In [ ]:
values_and_nulls(df,"Ingilizce Seviyeniz?")

In [ ]:
values_and_nulls(df,"Daha Önceden Mezun Olunduysa, Mezun Olunan Üniversite")

# ŞİMDİLİK 0 LAR İLE DOLDURACAĞIM SÜTUNLAR

In [ ]:
# ŞİMDİLİK 0 LAR İLE DOLDURACAĞIM SÜTUNLAR

# Daha Önceden Mezun Olunduysa, Mezun Olunan Üniversite
# Uye Oldugunuz Kulubun Ismi
# Lise Adi Diger
# Hangi STK'nin Uyesisiniz?
# Girisimcilikle Ilgili Deneyiminizi Aciklayabilir misiniz?
# Lise Bolum Diger